In [ ]:
# 1. Імпорти
import re
import math
from collections import defaultdict

import ipywidgets as widgets
from IPython.display import display, clear_output

# 2. Завантаження та попередня обробка
def preprocess_text(text):
    text = text.lower()
    # Видалити небажані символи, лишити тільки слова та пробіли
    text = re.sub(r'[^a-zа-яіїєґ0-9\s]', '', text)
    tokens = text.split()
    return tokens

# Припустимо, у вас є файл "corpus.txt" у середовищі Colab
with open('corpus.txt', 'r', encoding='utf-8') as f:
    raw_text = f.read()

tokens = preprocess_text(raw_text)

# 3. Побудова N-грам моделей
max_n = 5

# Зберігаємо частоти для кожного n
ngrams_freq = [defaultdict(int) for _ in range(max_n)]
context_freq = [defaultdict(int) for _ in range(max_n)]

def get_ngrams(tokens, n):
    return [tuple(tokens[i:i+n]) for i in range(len(tokens)-n+1)]

for n in range(1, max_n+1):
    ngrams = get_ngrams(tokens, n)
    for gram in ngrams:
        ngrams_freq[n-1][gram] += 1
        if n > 1:
            context = gram[:-1]
            context_freq[n-1][context] += 1

# 4. Функція розрахунку ймовірностей для передбачення наступного слова
def ngram_probability(next_word, context):
    """
    next_word: слово, яке прогнозуємо (str)
    context: кортеж з n-1 слів (для n-грам)
    повертає ймовірність P(next_word | context)
    Використовується простий метод MLE без згладжування
    """
    n = len(context) + 1
    if n == 1:
        # Уніграми
        total = sum(ngrams_freq[0].values())
        return ngrams_freq[0].get((next_word,), 0) / total if total > 0 else 0
    else:
        context_count = context_freq[n-1].get(context, 0)
        if context_count == 0:
            # Якщо контекст відсутній, повертаємо 0
            return 0
        return ngrams_freq[n-1].get(context + (next_word,), 0) / context_count

# 5. Функція автозавершення - пропонує найбільш ймовірні слова з backoff
def autocomplete(input_text, top_k=5):
    input_tokens = preprocess_text(input_text)
    suggestions = []

    # Починаємо з максимальної n-грами і поступово зменшуємо n
    for n in range(max_n, 0, -1):
        if len(input_tokens) >= n - 1:
            context = tuple(input_tokens[-(n - 1):]) if n > 1 else tuple()
            candidates = []

            for gram, freq in ngrams_freq[n - 1].items():
                if n == 1 or gram[:-1] == context:
                    next_word = gram[-1]
                    prob = ngram_probability(next_word, context)
                    if prob > 0:
                        candidates.append((next_word, prob))

            if candidates:
                candidates = sorted(candidates, key=lambda x: x[1], reverse=True)[:top_k]
                suggestions = [w for w, p in candidates]
                break

    # Якщо навіть уніграми не дали результатів, беремо топ-5 найчастотніших уніграм
    if not suggestions:
        unigram_freq = ngrams_freq[0]
        most_common = sorted(unigram_freq.items(), key=lambda x: x[1], reverse=True)[:top_k]
        suggestions = [w[0] for w, _ in most_common]

    return suggestions if suggestions else ["Немає пропозицій"]

# 6. Обчислення перплексії
def perplexity(test_tokens):
    N = len(test_tokens)
    if N == 0:
        return float('inf')

    log_prob_sum = 0
    for i in range(N):
        start = max(0, i - (max_n - 1))
        context = tuple(test_tokens[start:i])
        if len(context) < max_n - 1:
            context = context[-(max_n-1):]
        word = test_tokens[i]
        prob = 0
        for n in range(max_n, 0, -1):
            ctx = context[-(n-1):] if n > 1 else tuple()
            p = ngram_probability(word, ctx)
            if p > 0:
                prob = p
                break
        if prob == 0:
            prob = 1e-10
        log_prob_sum += math.log(prob)

    ppl = math.exp(-log_prob_sum / N)
    return ppl

# 7. Простий UI для тестування з ipywidgets
input_box = widgets.Text(
    value='',
    placeholder='Введіть текст для автозавершення',
    description='Вхід:',
    disabled=False,
    layout=widgets.Layout(width='70%')
)

output_box = widgets.Output()

def on_text_change(change):
    with output_box:
        clear_output()
        text = change['new']
        suggestions = autocomplete(text, top_k=5)
        print("Пропозиції для наступного слова:")
        for i, word in enumerate(suggestions, 1):
            print(f"{i}. {word}")

input_box.observe(on_text_change, names='value')

display(input_box, output_box)


Text(value='', description='Вхід:', layout=Layout(width='70%'), placeholder='Введіть текст для автозавершення'…

Output()

In [ ]:
import json

# Для серіалізації ключів (які у нас кортежі) треба перетворити їх у строки
def serialize_ngrams(ngrams_dict):
    return { ' '.join(k): v for k, v in ngrams_dict.items() }

# Зберігаємо частоти у словник для збереження в json
model_to_save = {}
for n in range(max_n):
    model_to_save[f'{n+1}-gram'] = serialize_ngrams(ngrams_freq[n])

# Запис у файл
with open('ngram_model.json', 'w', encoding='utf-8') as f:
    json.dump(model_to_save, f, ensure_ascii=False, indent=2)


In [ ]:
# Завантаження
with open('ngram_model.json', 'r', encoding='utf-8') as f:
    loaded_model = json.load(f)

# Перегляд ключів (приклад для 3-грам)
print("Ключі 3-грам моделі (перші 100):")
for i, k in enumerate(list(loaded_model['3-gram'].keys())[:10]):
    print(k, ":", loaded_model['3-gram'][k])


Ключі 3-грам моделі (перші 100):
замкнена кімната пер : 1
кімната пер вале : 1
пер вале май : 1
вале май шеваль : 1
май шеваль пер : 1
шеваль пер вале : 1
пер вале замкнена : 1
вале замкнена кімната : 1
замкнена кімната переклад : 1
кімната переклад ольги : 1


In [ ]:
import json

# Завантаження файлу (запустити, якщо ще не завантажив)
from google.colab import files
uploaded = files.upload()  # Обери ngram_model.json

# Читання JSON
with open('ngram_model.json', 'r', encoding='utf-8') as f:
    ngram_model = json.load(f)

# Перевірка кількох прикладів
for i, (context, suggestions) in enumerate(ngram_model.items()):
    print(f"{context!r} → {suggestions}")
    if i >= 9:  # показати тільки перші 10
        break


Saving ngram_model.json to ngram_model (1).json
'1-gram' → {'замкнена': 10, 'кімната': 15, 'пер': 4, 'вале': 2, 'май': 1, 'шеваль': 1, 'переклад': 1, 'ольги': 1, 'сенюк': 1, 'i': 1, 'на': 1310, 'вежі': 2, 'маріїнської': 4, 'церкви': 3, 'вибило': 2, 'другу': 7, 'годину': 13, 'коли': 331, 'вона': 395, 'вийшла': 9, 'з': 801, 'метро': 17, 'станції': 9, 'вольмарікскюлсгатан': 1, 'зупинившись': 1, 'закурила': 3, 'тоді': 163, 'швидко': 39, 'рушила': 7, 'в': 1052, 'бік': 21, 'площі': 12, 'відгомін': 1, 'дзвону': 1, 'що': 1231, 'тремтів': 1, 'у': 684, 'повітрі': 3, 'нагадав': 2, 'їй': 66, 'безрадісні': 1, 'неділі': 2, 'дитинства': 2, 'народилась': 4, 'і': 1578, 'виросла': 1, 'всього': 11, 'за': 354, 'кілька': 67, 'кварталів': 1, 'від': 136, 'там': 122, 'її': 234, 'хрестили': 1, 'майже': 52, 'дванадцять': 7, 'років': 55, 'тому': 107, 'відбула': 1, 'конфірмацію': 1, 'із': 168, 'тієї': 26, 'події': 7, 'запамяталось': 1, 'тільки': 182, 'одне': 38, 'як': 378, 'спитала': 20, 'пастора': 1, 'мав': 62, 

In [ ]:
import json
from collections import defaultdict

# Завантаження моделі
with open('ngram_model.json', 'r', encoding='utf-8') as f:
    raw_model = json.load(f)

autocomplete_model = defaultdict(set)

# Проходимо по всіх n-грамах, починаючи з 2-грам (щоб був контекст)
for ngram_key in raw_model:
    if ngram_key == '1-gram':
        continue  # пропускаємо 1-грам, бо немає контексту
    ngram_dict = raw_model[ngram_key]
    for ngram, count in ngram_dict.items():
        tokens = ngram.split()
        if len(tokens) < 2:
            continue
        context = ' '.join(tokens[:-1])
        next_word = tokens[-1]
        autocomplete_model[context].add(next_word)

# Перетворюємо множини у списки для JSON
autocomplete_model = {k: list(v) for k, v in autocomplete_model.items()}

# Збереження автозавершення у JSON файл
with open('autocomplete_model.json', 'w', encoding='utf-8') as f:
    json.dump(autocomplete_model, f, ensure_ascii=False, indent=2)

# Перевірка — виведемо перші 10 елементів
for i, (context, suggestions) in enumerate(autocomplete_model.items()):
    print(f"{context!r} → {suggestions}")
    if i >= 9:
        break


'замкнена' → ['кімната', 'зсередини', 'валіза']
'кімната' → ['двері', 'про', 'не', 'маленька', 'розслідування', 'непогано', 'коли', 'з', 'дитяча', 'пер', 'була', 'письмовий', 'переклад']
'пер' → ['монсон', 'вале']
'вале' → ['май', 'замкнена']
'май' → ['шеваль']
'шеваль' → ['пер']
'переклад' → ['ольги']
'ольги' → ['сенюк']
'сенюк' → ['i']
'i' → ['на']


In [ ]:
from google.colab import files
files.download('autocomplete_model.json')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
!ls -l autocomplete_model.json


-rw-r--r-- 1 root root 13325102 May 28 17:02 autocomplete_model.json


In [ ]:
!cat autocomplete_model.json


{}